# Part 1: Software Implementation of Birdsong Separation Using FIR Filters

## 1. Introduction

In this chapter, we are given a piece of audio with two bird sounds mixed in. Through the human ear, we can simply distinguish the two sounds. Then you can think about how, through technical means, you can turn this piece of audio mixed with two bird sounds into two pieces of audio with separate bird sounds? After studying this chapter, you will have the answer.

The purpose of this chapter is to separate the two bird sounds in the audio and get separate bird sounds. To achieve this, we will use C++ language to write FIR filter for separation at HLS (high level synthesis) level, and use parallel and pipelined hardware design ideas and AXI4 data transfer protocol to perform hardware acceleration on PYNQ board. We also use python for software code writing to show the advantages of hardware acceleration after comparing the two.

### 1.1 What is FIR Filter? 

Finite Impulse Response Filter (FIR), a non-recursive filter, is also a widely used signal processing tool. The figure below shows how it works. The signal is passed through an analog-to-digital converter (A/D). After the control signal is given by the FIR Controller, the filtered signal is obtained by Adder, Multiplier, Accumulator, etc. and finally output by Digital to Analog (D/A) conversion.

<img src="./image/FIR_work_principle.png" alt="FIR_work_principle.png" style="zoom:70%;" />

The FIR filter is characterized by the fact that its output depends on the input x[n] at that time, the input x[0:n-1] in the past and the selection of the tap coefficients h[0:n]. Here we can look at the tap coefficients as weights, i.e., the relative importance of each time period for the value at the current time, or the discrete shock response. In general, the tap coefficients are even or odd symmetric, which makes the filter linear in phase. The order of the FIR filter is the number of coefficients plus one. After the algorithm is calculated, the result is a linear combination of the previous inputs and the current inputs. Assuming that the filter order is k+1, it can be expressed by the following equation.
$$
y[n] = h[0]x[n-0] + h[1]x[n-1]+···+h[k]x[n-k]
$$
We can simply understand it as follows: the coefficients h[m] are used as weights and multiplied with the signals x[n] at different time points, so that n products can be obtained. Then all these products are accumulated, and the result is the signal output at a certain time point of the FIR filter. That is, the signal is shifted stage by stage with delay and then the delayed outputs of each stage are weighted and accumulated.

The figure below is an example. h[k] is the tapped coefficient, and we can see that the coefficients only have values at k=0 and k=1. Each addition of 1 to n is a translation of the x function to the right by 1 bit. When n<0, x[n-k] only has values at the negative half-axis in the state of k<0, so the values of h[k] and x[n-k] are staggered from each other and multiplied and accumulated to 0. When n=0, both h[k] and x[0-k] have values at k=0, so $y[0]=x[0]h[0] =1 \times 1=1$. When n=1, both h[k] and x[1-k] have values at k=0,k = 1, so $y[1] = x[0]h[0] + x[1]h[1] = 2\times 1+1\times 1 = 3$. When n=1, h[k] and x[2-k] both have values at k=0,k=1, so $y[1] = x[0]h[0] + x[1]h[1] = 3\times 1+2\times 2 = 7$.

<img src="./image/calculate_steps.png" alt="calculate_steps.png" style="zoom:70%;" />

Thus, it seems that the mathematical calculations used in the FIR filter are addition and multiplication. The corresponding hardware implementation is the adder and multiplier. In FPGA, we have a large number of regular internal logic arrays and abundant wire resources. The process of FIR filter is shown in the figure below.

<img src="./image/The_hardware_structure_of_the_FIR.png" alt="The_hardware_structure_of_the_FIR.png" style="zoom:70%;" />

According to the above flow, first the current signal x[n] is multiplied with the coefficient h[0], x[n-1] is multiplied with the coefficient h[1], and the results of both are accumulated. x[n-2] is multiplied with the coefficient h[2] and the results are again accumulated, and so on and so forth until finally multiplied with x[n-k] and the coefficient h[k] for the last accumulation. The final answer is the filtered signal for the current point in time.


## 2. Using Spectrogram to Show the Frequency of Two Bird Species

First you need a PYNQ board and a configured environment. You can refer to our official github documentation at https://github.com/Xilinx/PYNQ_Bootcamp/tree/master/doc. There are tutorials here to give you a quick overview of how to get your board up and running in the proper development environment, as well as having guides on setting up network connections and troubleshooting common network errors.

### 2.1 Audio Signal Demonstration

First let's import the audio. We can use the interactive feature of jupyter notebook to hear the sounds of two birds interspersed with the audio. The bird with a lower frequency and shorter chirp duration is
the Eurasian curlew; the bird with a higher frequency and longer chirp duration is the chaffinch.  


In [3]:
from scipy.io import wavfile

fs, aud_in = wavfile.read("./media/birds.wav")

After visualization, we can use the `spectrogram` function of the interactive plotting `scipy` library to present the audio in the frequency domain using data visualization.

In [5]:
import numpy as np
import warnings
warnings.simplefilter(action='ignore', category=FutureWarning)

import plotly.graph_objs as go  
import plotly.offline as py  
from scipy.signal import spectrogram, decimate  
	  
def plot_spectrogram(samples, fs, decimation_factor=3, max_heat=50, mode='2D'):  
	  
    # Optionally decimate input  
    if decimation_factor>1:  
        samples_dec = decimate(samples, decimation_factor, zero_phase=True)  
        fs_dec = int(fs / decimation_factor)  
    else:  
        samples_dec = samples  
        fs_dec = fs  
	  
    # Calculate spectrogram (an array of FFTs from small windows of our signal)  
    f_label, t_label, spec_data = spectrogram(  
        samples_dec, fs=fs_dec, mode="magnitude"  
    )  
	  
    # Make a plotly heatmap/surface graph  
    layout = go.Layout(  
        height=500,  
        # 2D axis titles  
        xaxis=dict(title='Time (s)'),  
        yaxis=dict(title='Frequency (Hz)'),  
        # 3D axis titles  
        scene=dict(  
            xaxis=dict(title='Time (s)'),  
            yaxis=dict(title='Frequency (Hz)'),  
            zaxis=dict(title='Amplitude')  
        )  
    )  
	  
    trace = go.Heatmap(  
        z=np.clip(spec_data,0,max_heat),  
        y=f_label,  
        x=t_label  
    ) if mode=='2D' else go.Surface(  
        z=spec_data,  
        y=f_label,  
        x=t_label  
    )  
	  
    py.iplot(dict(data=[trace], layout=layout))  
	  
plot_spectrogram(aud_in, fs, mode='2D') 

Through a spectrogram, we can clearly distinguish the sounds of two different bird species. The voice of a Eurasian curlew is located between 1.2-2.6kHz, while the voice of a chaffinch is between 3-5kHz.
In order to filter out the sound of the Eurasian curlew between 1.2-2.6kHz, we need a high-pass filter with a cutoff frequency of 2.6kHz. To leave some margin, this cutoff frequency can be set to 2.8kHz. At the same time you also choose to filter chaffinch sounds between 3-5kHz, both can be achieved. In this chapter, we will implement the former.  

## 3. Software Implementation of FIR Using Scipy Library

In Python, we use the Scipy library and the Numpy library in concert. First we use Scipy's firwin function to get the FIR filter tap coefficients by specifying the filter order, target cutoff frequency, etc.

After that, we input the tap coefficients into the lfilter function of the Scipy library, specify the audio file, and finally get the filtered signals.


In [7]:
from scipy.signal import freqz, firwin  
	  
nyq = fs / 2.0  
taps = 99  
	  
# Design high-pass filter with cut-off at 2.8 kHz  
hpf_coeffs = firwin(taps, 2800/nyq, pass_zero=False)  
	  
from scipy.signal import lfilter  
import time  
  
start_time = time.time()  
# Filter audio  
aud_hpf = lfilter(hpf_coeffs, 1.0, aud_in)  
end_time = time.time()  
print("Time cost with Python：{}s".format(end_time - start_time)) 

plot_spectrogram(aud_hpf, fs, mode='2D', max_heat=np.max(abs(aud_hpf)))

Time cost with Python：0.016100406646728516s


After filtering, the Eurasian curlew sound has disappeared from the spectrogram. We can see that the filtering time using the software is about 0.459 seconds. The performance is highly dependent on the `Ifilter` function, and generally such functions are highly optimized and put into the library, which can be easily implemented by the user by tuning the library, but there is very little room for self-optimization. In this case, if further performance improvements are desired, hardware modules can be used instead of software algorithms to take advantage of the fast nature inherent in hardware.

---------------------------------------
<p align="center">Copyright&copy; 2024 Advanced Micro Devices</p>